In [1]:
import requests
import pandas as pd
import pymysql
import numpy as np
import time
from datetime import datetime, timedelta
import traceback2

In [2]:
def get_data_from_host(url, retry_count=0):
    try:
        r = requests.get(url)
        return r.json()
    except Exception as e:
        print(e)
        print(r)
        if retry_count < 3:
            time.sleep(1)
            return get_data_from_host(url, retry_count=retry_count + 1)
    return None

In [3]:
def __connect__():
    db_user = 'coin'
    db_password = 'dragonstone#123'
    db_name = 'master_data'
    db_host = 'localhost'
    return pymysql.connect(
        unix_socket=None,
        host=db_host,
        user=db_user,
        password=db_password,
        db=db_name,
        charset='latin1',
        cursorclass=pymysql.cursors.DictCursor)


def get_cursor(connection):
    if connection is None:
        connection = __connect__()
    connection.ping(reconnect=True)
    return connection.cursor()

In [4]:
def insert_debank_projects_data_df(df):
    connection = __connect__()
    cursor = get_cursor(connection)
    for i, row in df.iterrows():
        dt = row["date"].timestamp()
        try:
            print(row["date"], row["symbol"], row["project"], row["tvl"], row["trade_users"], row["trade_volume"], row["trade_count"], row["oncall_contract"], row["oncall_call"], row['borrow'], row['active_user_24h'])
            sql = """INSERT INTO `debank_project_data_v2` (`timestamp_dt`, `project`, `tvl`, `trading_users`, `trading_volume`, `transactions`, `call_contract`, `number_of_calls`, `borrow`, `active_user_24h`, `project_id`) VALUES (FROM_UNIXTIME(%s), %s, %s, %s, %s, %s, %s, %s, %s, %s, %s)
                ON DUPLICATE KEY UPDATE
                `tvl` = VALUES(tvl),
                `trading_users` = VALUES(trading_users),
                `trading_volume` = VALUES(trading_volume),
                `transactions` = VALUES(transactions),
                `call_contract` = VALUES(call_contract),
                `number_of_calls` = VALUES(number_of_calls),
                `active_user_24h` = VALUES(active_user_24h),
                `borrow` = VALUES(borrow)
            """
            cursor.execute(sql, (dt, row["project"], row["tvl"], row["trade_users"], row["trade_volume"], row["trade_count"], row["oncall_contract"], row["oncall_call"], row['borrow'], row['active_user_24h'], row["symbol"]))
        except Exception:
            print(traceback2.format_exc())
            pass
    connection.commit()
    cursor.close()
    connection.close()


In [5]:
def get_tvl():
    url = 'https://static1.debank.com/tvl/projects-v2.json'
    data = get_data_from_host(url)
    dfs = pd.DataFrame([])
    for d1 in data:
        df = pd.DataFrame(d1['data'])
        df = df[['date_at', 'locked_usd_value']]
        df.columns = ['date', 'tvl']
        df['symbol'] = d1['id']
        dfs = dfs.append(df)
    return dfs.reset_index(drop=True)

In [6]:
def get_dex_data():
    dex_histori_api = 'https://api.debank.com/old/dex/histories'
    # dex_chart_api = 'https://api.debank.com/old/dex/charts'
    data = get_data_from_host(dex_histori_api)['data']
    dex_df = pd.DataFrame
    for row in data:
        df = pd.DataFrame(row['dates'])
        if dex_df.empty:
            dex_df = df
        else:
            dex_df = dex_df.append(df)
    columns = ['active_user_count', 'amount', 'count', 'project_id', 'date_at']
    dex_df = dex_df[columns]
    dex_df.columns = ['trade_users', 'trade_volume', 'trade_count', 'symbol', 'date']
    return dex_df.reset_index(drop=True)

In [7]:
def get_lending_data():
    lending_api = 'https://api.debank.com/debt/borrow_amount/date'
    data = get_data_from_host(lending_api)['data']
    lending_df = pd.DataFrame
    for key in data:
        key_data = data[key]
        df = pd.DataFrame(key_data)
        df['symbol'] = key
        if lending_df.empty:
            lending_df = df
        else:
            lending_df = lending_df.append(df)
    lending_df.columns = ['date', 'borrow', 'symbol']
    return lending_df.reset_index(drop=True)

In [8]:
def get_oracle_contract_count_data():
    oracle_contract_count_api = 'https://api.debank.com/oracle/contract_count/date'
    data = get_data_from_host(oracle_contract_count_api)['data']
    oracle_contract_count_df = pd.DataFrame([])
    for key in data:
        key_data = data[key]
        df = pd.DataFrame(key_data)
        df['symbol'] = key
        oracle_contract_count_df = oracle_contract_count_df.append(df)
    oracle_contract_count_df.columns = ['date', 'oncall_contract', 'symbol']
    return oracle_contract_count_df

In [9]:
def get_oracle_call_count_data():
    oracle_date_api = 'https://api.debank.com/oracle/call_count/date'
    data = get_data_from_host(oracle_date_api)['data']
    oracle_call_count_df = pd.DataFrame([])
    for key in data:
        key_data = data[key]
        df = pd.DataFrame(key_data)
        df['symbol'] = key
        oracle_call_count_df = oracle_call_count_df.append(df)
    oracle_call_count_df.columns = ['date', 'oncall_call', 'symbol']
    return oracle_call_count_df

In [10]:
def get_orcale_data():
    contract_count_df = get_oracle_contract_count_data()
    call_count_df = get_oracle_call_count_data()
    df = pd.merge(contract_count_df, call_count_df, how='outer', left_on=['date', 'symbol'], right_on=['date', 'symbol'])
    df = df[['date', 'symbol', 'oncall_contract', 'oncall_call']]
    return df


In [11]:
def get_name_df():
    project_list_url = 'https://api.debank.com/project/v2/list'
    data = get_data_from_host(project_list_url)['data']
    rows = []
    for row in data:
        rows.append([row['id'], row['name']['en'], row['active_user_count_24h']])
    name_df = pd.DataFrame(rows, columns=['symbol', 'project', 'active_user_24h'])
    return name_df

In [12]:
def get_debank_home_page_data():
    today = datetime.now()
    today = datetime(today.year, today.month, today.day)
    oracel = get_orcale_data()
    lendings = get_lending_data()
    dex = get_dex_data()
    tvl = get_tvl()
    name_df = get_name_df()
    df = pd.merge(oracel, lendings, how='outer', left_on=['date', 'symbol'], right_on=['date', 'symbol'])
    df = pd.merge(df, dex, how='outer', left_on=['date', 'symbol'], right_on=['date', 'symbol'])
    df = pd.merge(df, tvl, how='outer', left_on=['date', 'symbol'], right_on=['date', 'symbol'])
    df = pd.merge(name_df, df, how='outer', left_on=['symbol'], right_on=['symbol'])
    del df['active_user_24h']
    df['date'] = df['date'].fillna(today)
    df['date'] = pd.to_datetime(df['date'])
    name_df['date'] = today
    name_df['date'] = pd.to_datetime(name_df['date'])
    df = pd.merge(name_df, df, how='outer', left_on=['date','symbol', 'project'], right_on=['date','symbol', 'project'])
    df['date'] = df['date'].fillna(today)
    df = df.sort_values(['symbol', 'date']).reset_index(drop=True)
    df = df.astype(object).where(pd.notnull(df), None)
    return df

In [13]:
debank_df = get_debank_home_page_data()

In [14]:
debank_df['date']

0        2021-07-05 00:00:00
1        2021-07-05 00:00:00
2        2020-11-04 00:00:00
3        2020-11-05 00:00:00
4        2020-11-06 00:00:00
                ...         
70046    2021-07-01 00:00:00
70047    2021-07-02 00:00:00
70048    2021-07-03 00:00:00
70049    2021-07-04 00:00:00
70050    2021-07-05 00:00:00
Name: date, Length: 70051, dtype: object

In [15]:
insert_debank_projects_data_df(debank_df)

2021-07-05 00:00:00 0x 0x None None None None None None None 924.0
2021-07-05 00:00:00 1inch 1inch V1 None None None None None None None 296.0
2020-11-04 00:00:00 1inch2 1inch 0.0 2.0 4.408874 2.0 None None None None
2020-11-05 00:00:00 1inch2 1inch 0.0 359.0 7878227.61552862 533.0 None None None None
2020-11-06 00:00:00 1inch2 1inch 0.0 698.0 34350914.96027924 1311.0 None None None None
2020-11-07 00:00:00 1inch2 1inch 0.0 667.0 36016449.38945731 1371.0 None None None None
2020-11-08 00:00:00 1inch2 1inch 0.0 628.0 18948459.074073084 1116.0 None None None None
2020-11-09 00:00:00 1inch2 1inch 0.0 696.0 23120946.3751728 1307.0 None None None None
2020-11-10 00:00:00 1inch2 1inch 0.0 685.0 32734675.166491996 1533.0 None None None None
2020-11-11 00:00:00 1inch2 1inch 0.0 762.0 22357625.165226866 1358.0 None None None None
2020-11-12 00:00:00 1inch2 1inch 0.0 649.0 24656391.967546277 1239.0 None None None None
2020-11-13 00:00:00 1inch2 1inch 0.0 629.0 27615123.787595168 1203.0 None None

2021-03-18 00:00:00 1inch2 1inch 401390911.66894656 1503.0 156733565.98549703 2599.0 None None None None
2021-03-19 00:00:00 1inch2 1inch 432101039.5659675 1807.0 169895995.88639703 3159.0 None None None None
2021-03-20 00:00:00 1inch2 1inch 437461616.9916447 2041.0 114639874.85821544 3479.0 None None None None
2021-03-21 00:00:00 1inch2 1inch 429226331.8090863 1955.0 134937462.36246395 3472.0 None None None None
2021-03-22 00:00:00 1inch2 1inch 411365139.96810085 1801.0 145189348.69947803 3152.0 None None None None
2021-03-23 00:00:00 1inch2 1inch 396606814.13406605 1522.0 189944068.3420059 2836.0 None None None None
2021-03-24 00:00:00 1inch2 1inch 358759971.03972584 1459.0 159637798.66923666 2549.0 None None None None
2021-03-25 00:00:00 1inch2 1inch 349609049.0758025 1466.0 159794740.17941907 2535.0 None None None None
2021-03-26 00:00:00 1inch2 1inch 373204281.17842436 1585.0 116363220.3507673 2549.0 None None None None
2021-03-27 00:00:00 1inch2 1inch 385017723.1895132 1671.0 162

2020-12-06 00:00:00 88mph 88mph V1 166137.9446682167 None None None None None None None
2020-12-07 00:00:00 88mph 88mph V1 166254.50861288808 None None None None None None None
2020-12-08 00:00:00 88mph 88mph V1 165849.60762095387 None None None None None None None
2020-12-09 00:00:00 88mph 88mph V1 165839.30484022904 None None None None None None None
2020-12-10 00:00:00 88mph 88mph V1 165691.0791266855 None None None None None None None
2020-12-11 00:00:00 88mph 88mph V1 165431.56614618754 None None None None None None None
2020-12-12 00:00:00 88mph 88mph V1 165645.48204793542 None None None None None None None
2020-12-13 00:00:00 88mph 88mph V1 165914.30176238384 None None None None None None None
2020-12-14 00:00:00 88mph 88mph V1 165791.11501613492 None None None None None None None
2020-12-15 00:00:00 88mph 88mph V1 165757.91636608882 None None None None None None None
2020-12-16 00:00:00 88mph 88mph V1 165810.5561544961 None None None None None None None
2020-12-17 00:00:00 88mp

2021-04-25 00:00:00 88mph 88mph V1 196691.230106866 None None None None None None None
2021-04-26 00:00:00 88mph 88mph V1 200578.72210380455 None None None None None None None
2021-04-27 00:00:00 88mph 88mph V1 202036.91498391022 None None None None None None None
2021-04-28 00:00:00 88mph 88mph V1 204682.33809686854 None None None None None None None
2021-04-29 00:00:00 88mph 88mph V1 203665.20005955145 None None None None None None None
2021-04-30 00:00:00 88mph 88mph V1 202805.54570543824 None None None None None None None
2021-05-01 00:00:00 88mph 88mph V1 202606.18241564065 None None None None None None None
2021-05-02 00:00:00 88mph 88mph V1 204830.74336503784 None None None None None None None
2021-05-03 00:00:00 88mph 88mph V1 204787.7996061957 None None None None None None None
2021-05-04 00:00:00 88mph 88mph V1 205550.7140895908 None None None None None None None
2021-05-05 00:00:00 88mph 88mph V1 204803.59529388614 None None None None None None None
2021-05-06 00:00:00 88mph

2021-03-09 00:00:00 88mph2 88mph V2 26840808.530715838 None None None None None None None
2021-03-10 00:00:00 88mph2 88mph V2 24716976.036707018 None None None None None None None
2021-03-11 00:00:00 88mph2 88mph V2 25245761.131895654 None None None None None None None
2021-03-12 00:00:00 88mph2 88mph V2 24870686.116714913 None None None None None None None
2021-03-13 00:00:00 88mph2 88mph V2 26350426.91794331 None None None None None None None
2021-03-14 00:00:00 88mph2 88mph V2 26875245.68600749 None None None None None None None
2021-03-15 00:00:00 88mph2 88mph V2 25390193.991543982 None None None None None None None
2021-03-16 00:00:00 88mph2 88mph V2 25045971.61570024 None None None None None None None
2021-03-17 00:00:00 88mph2 88mph V2 25022692.837934338 None None None None None None None
2021-03-18 00:00:00 88mph2 88mph V2 26417940.238897473 None None None None None None None
2021-03-19 00:00:00 88mph2 88mph V2 28961631.979138736 None None None None None None None
2021-03-20 00

...

2020-12-23 00:00:00 yield YIELD (yield.is) 524584.6623287024 None None None None None None None
2020-12-24 00:00:00 yield YIELD (yield.is) 524584.6623287024 None None None None None None None
2020-12-25 00:00:00 yield YIELD (yield.is) 632299.9572365554 None None None None None None None
2020-12-26 00:00:00 yield YIELD (yield.is) 931991.9150208596 None None None None None None None
2020-12-27 00:00:00 yield YIELD (yield.is) 931991.9150208596 None None None None None None None
2020-12-28 00:00:00 yield YIELD (yield.is) 920126.7049747538 None None None None None None None
2020-12-29 00:00:00 yield YIELD (yield.is) 1195328.5653570364 None None None None None None None
2020-12-30 00:00:00 yield YIELD (yield.is) 1165979.6952734082 None None None None None None None
2020-12-31 00:00:00 yield YIELD (yield.is) 1159611.7514954084 None None None None None None None
2021-01-01 00:00:00 yield YIELD (yield.is) 1136088.5255419628 None None None None None None None
2021-01-02 00:00:00 yield YIELD (yie

2021-05-15 00:00:00 yield YIELD (yield.is) 1603909.8202597082 None None None None None None None
2021-05-16 00:00:00 yield YIELD (yield.is) 1596067.9388074116 None None None None None None None
2021-05-17 00:00:00 yield YIELD (yield.is) 1596067.9388074116 None None None None None None None
2021-05-18 00:00:00 yield YIELD (yield.is) 1596067.9388074116 None None None None None None None
2021-05-19 00:00:00 yield YIELD (yield.is) 1547706.6249454115 None None None None None None None
2021-05-20 00:00:00 yield YIELD (yield.is) 1548845.0593504114 None None None None None None None
2021-05-21 00:00:00 yield YIELD (yield.is) 1451904.7017940031 None None None None None None None
2021-05-22 00:00:00 yield YIELD (yield.is) 1383752.4489550246 None None None None None None None
2021-05-23 00:00:00 yield YIELD (yield.is) 1165594.7645621581 None None None None None None None
2021-05-24 00:00:00 yield YIELD (yield.is) 1165594.7645621581 None None None None None None None
2021-05-25 00:00:00 yield YIEL

2021-03-17 00:00:00 yvs YVS 330971.941314995 None None None None None None None
2021-03-18 00:00:00 yvs YVS 331237.9299914204 None None None None None None None
2021-03-19 00:00:00 yvs YVS 444354.3826312099 None None None None None None None
2021-03-20 00:00:00 yvs YVS 447744.3457789574 None None None None None None None
2021-03-21 00:00:00 yvs YVS 520031.17546 None None None None None None None
2021-03-22 00:00:00 yvs YVS 543251.994587473 None None None None None None None
2021-03-23 00:00:00 yvs YVS 553350.608353269 None None None None None None None
2021-03-24 00:00:00 yvs YVS 527909.6119778095 None None None None None None None
2021-03-25 00:00:00 yvs YVS 480475.5779057759 None None None None None None None
2021-03-26 00:00:00 yvs YVS 471615.83491111966 None None None None None None None
2021-03-27 00:00:00 yvs YVS 471333.06192010414 None None None None None None None
2021-03-28 00:00:00 yvs YVS 449406.74870774656 None None None None None None None
2021-03-29 00:00:00 yvs YVS 44353

2021-02-05 00:00:00 zai ZAI V1 89224.52948938534 None None None None None None None
2021-02-06 00:00:00 zai ZAI V1 89799.15681438905 None None None None None None None
2021-02-07 00:00:00 zai ZAI V1 89212.97020474488 None None None None None None None
2021-02-08 00:00:00 zai ZAI V1 89317.1393448362 None None None None None None None
2021-02-09 00:00:00 zai ZAI V1 87108.07367309148 None None None None None None None
2021-02-10 00:00:00 zai ZAI V1 85154.45655179859 None None None None None None None
2021-02-11 00:00:00 zai ZAI V1 85679.7593989247 None None None None None None None
2021-02-12 00:00:00 zai ZAI V1 89238.67972240754 None None None None None None None
2021-02-13 00:00:00 zai ZAI V1 86120.79331727831 None None None None None None None
2021-02-14 00:00:00 zai ZAI V1 86079.15198939857 None None None None None None None
2021-02-15 00:00:00 zai ZAI V1 91253.66599255762 None None None None None None None
2021-02-16 00:00:00 zai ZAI V1 88233.5219755731 None None None None None None 

2021-02-26 00:00:00 zkswap ZKSwap 351056914.9258088 None None None None None None None
2021-02-27 00:00:00 zkswap ZKSwap 174979142.61824235 None None None None None None None
2021-02-28 00:00:00 zkswap ZKSwap 176496880.96176377 None None None None None None None
2021-03-01 00:00:00 zkswap ZKSwap 182056065.82518214 None None None None None None None
2021-03-02 00:00:00 zkswap ZKSwap 171876712.56649053 None None None None None None None
2021-03-03 00:00:00 zkswap ZKSwap 196903832.42776206 None None None None None None None
2021-03-04 00:00:00 zkswap ZKSwap 254193001.52390498 None None None None None None None
2021-03-05 00:00:00 zkswap ZKSwap 232265892.54946396 None None None None None None None
2021-03-06 00:00:00 zkswap ZKSwap 464428595.077899 None None None None None None None
2021-03-07 00:00:00 zkswap ZKSwap 547959108.7729445 None None None None None None None
2021-03-08 00:00:00 zkswap ZKSwap 647303568.0414554 None None None None None None None
2021-03-09 00:00:00 zkswap ZKSwap 818

In [16]:
debank_df

symbol   project active_user_24h                 date oncall_contract  \
0          0x        0x           924.0  2021-07-05 00:00:00            None   
1       1inch  1inch V1           296.0  2021-07-05 00:00:00            None   
2      1inch2     1inch            None  2020-11-04 00:00:00            None   
3      1inch2     1inch            None  2020-11-05 00:00:00            None   
4      1inch2     1inch            None  2020-11-06 00:00:00            None   
...       ...       ...             ...                  ...             ...   
70046  zkswap    ZKSwap            None  2021-07-01 00:00:00            None   
70047  zkswap    ZKSwap            None  2021-07-02 00:00:00            None   
70048  zkswap    ZKSwap            None  2021-07-03 00:00:00            None   
70049  zkswap    ZKSwap            None  2021-07-04 00:00:00            None   
70050  zkswap    ZKSwap            18.0  2021-07-05 00:00:00            None   

      oncall_call borrow trade_users     trade_volume trade_count  \
0            None   None        None             None        None   
1            None   None        None             None        None   
2            None   None         2.0         4.408874         2.0   
3            None   None       359.0   7878227.615529       533.0   
4            None   None       698.0  34350914.960279      1311.0   
...           ...    ...         ...              ...         ...   
70046        None   None        None             None        None   
70047        None   None        None             None        None   
70048        None   None        None             None        None   
70049        None   None        None             None        None   
70050        None   None        None             None        None   

                   tvl  
0                 None  
1                 None  
2                  0.0  
3                  0.0  
4                  0.0  
...                ...  
70046  88759146.290066  
70047   88385142.08705  
70048  91212743.947213  
70049  91456561.175749  
70050  90330681.489744  

[70051 rows x 11 columns]

In [17]:
name_df = get_name_df()

In [18]:
debank_df[debank_df['project'] == 'Badger DAO']

symbol     project active_user_24h                 date  \
4484      badger  Badger DAO           146.0  2021-07-05 00:00:00   
8084  bsc_badger  Badger DAO            32.0  2021-07-05 00:00:00   

     oncall_contract oncall_call borrow trade_users trade_volume trade_count  \
4484            None        None   None        None         None        None   
8084            None        None   None        None         None        None   

       tvl  
4484  None  
8084  None